In [1]:
from queue import Queue

from unidecode import unidecode
import networkx as nx
import spotipy #https://spotipy.readthedocs.io/en/latest/
from spotipy.oauth2 import SpotifyClientCredentials

/home/chends/.local/lib/python3.6/site-packages/requests/__init__.py:91: RequestsDependencyWarning: urllib3 (1.24.1) or chardet (3.0.4) doesn't match a supported version!
  RequestsDependencyWarning)


In [2]:
# Charles profile link:
# https://open.spotify.com/user/12167056236?si=BfbG8v9wRsOTnilpjP9ibg
# spotify:user:12167056236:playlist:1ahkvZq6vSkYCmqHiPpLJn
charles_id = '12167056236'

# Jazz playlist link:
# https://open.spotify.com/user/12167056236/playlist/2ek4gj4PDBF4aspnYWfBmC?si=eq_YK6V8SdKiuhu1zj5VPA
# spotify:user:12167056236:playlist:2ek4gj4PDBF4aspnYWfBmC
jazz_id = '2ek4gj4PDBF4aspnYWfBmC'

# Bossa nova playlist link:
# https://open.spotify.com/user/12167056236/playlist/1ahkvZq6vSkYCmqHiPpLJn?si=DQT4XTRYSwWagYejOs34Ew
bossanova_id = '1ahkvZq6vSkYCmqHiPpLJn'

In [3]:
# client_credentials_manager = SpotifyClientCredentials(client_id='943e4795c796489f9243c6e7c9f64fc7', client_secret='c6c980434cb74acc9a7408e5c99618b1')
# sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)
# spotify:user:12167056236:playlist:2ek4gj4PDBF4aspnYWfBmC

In [4]:
# playlists = sp.user_playlists('spotify')
# tracks = user_playlist_tracks(user = 12167056236, playlist_id=2ek4gj4PDBF4aspnYWfBmC?si=j-MSydgGR1O3KgIUea6Yzw)

In [5]:
client_credentials_manager = SpotifyClientCredentials(client_id='943e4795c796489f9243c6e7c9f64fc7', client_secret='c6c980434cb74acc9a7408e5c99618b1')
sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)

# def calc_feat_dict(results):
#     artists_musics = {}
#     for i, item in enumerate(results['items']):
#         track = item['track']
#         artists_musics[track['artists'][0]['name']] = (track['name'].split(" - ")[0])
#         #print(track['id'])
#         #print("%d: %s - %s" % (i, track['artists'][0]['name'], track['name'].split(" - ")[0]))
#     return artists_musics

def calc_tuple(results):
    artists_musics = []
    for i, item in enumerate(results['items']):
        track = item['track']
        artists_musics.append((track['artists'][0]['id'], track['artists'][0]['name'], track['id'], track['name']))
        #print((track['artists'][0]['name'], (track['name'].split(" - ")[0])))
    return artists_musics

In [7]:
art_mus = {}

results = sp.user_playlist(user = charles_id, playlist_id = jazz_id, fields = "tracks, next")
tracks = results['tracks']

while tracks['next']: #passa pelos 10 conjuntos de tracks
    tracks = sp.next(tracks)
    data = calc_tuple(tracks)    
    
    #inicializa o dicio com o primeiro artista deste cojunto
    for i in range(len(data)): #rodará 100 vezes
        if data[i][1] not in art_mus.keys(): #trocou artista
            art_mus[data[i][1]] = [data[i][2]]         
        else: #mesmo artista
            art_mus[data[i][1]].append(data[i][2])

artistas = 119
print(art_mus)

{'Shorty Rogers': ['7eFl80yr1Q8uOpCK2MqVVP', '4AH2V817mRZTrPABae4upz', '5nHqWtiqYnCggjsBeTvc7t', '084CU56jKdwuOV3p4jDMJh', '7CFiMlBahoknsuP9oo84zO', '1dEvMRtPhuEXWHW1bBNpPD', '0jN00EUhWfrYytfKP7VtJm', '7ruvTFooRENXdwAPA0z1io', '03DGhW3ZxBZCJyyPwKKwGw', '6ILVFqII1kO4lolYLvkl5G', '35FFgvQKFpRgNqm6EKVo3l', '3Ue41Ts5phLmsdVAetfVMU', '22rjKEQJZOUwx7hfLnq5UJ', '4YJ4Okkqpb3Ajx01ZJxnwO', '1BdBPEGH6b76XQG5SFaaFz', '1plvAv8LKXE2Qa9IMGlcC1', '2VBdWuqKbG2mL3ky4RdFb5', '6hXQhvqb5qqYZKBkEGBRvx', '2H5C4BTNjBplzW9Dxclvr4'], 'Herb Ellis': ['6cqdRr2F4q39Crzhrt5ZXP', '0b0jjQbfHi2e1JddxnuBNi', '4s4LE92YZ8m55dCdbYNRLO', '4NvyL6yEHxcp61WCEvqYGe', '1sXZUtiK6rO9DbBZvTr3YP', '72RqVL6vuG2QGnXRu2Zydc', '6de9mBhTv18hcVA7c9LBN1', '6lsWG50ZMtGLRXiFLNg44X', '6orvYfmrCeI8QUcphfIyqI', '4Hlhm43upltEuc1A1Pcfs4', '4ewfvy3ibc0KIdJroXTrcz', '6OyNsvLPEY8cMNLSVv6si7', '2D4wbJfkrtmSJwz7F8yklT', '5w2p46WgLL3GrmntKyh03b', '0UBw5Xn3MPK8Yl4YO3XIzw', '2utGJya4J7VSP42xmWPjec', '7uy5CWdttvnij3SdhUxrun', '1yzHmDkO299Z2IGPtC8yPG', '4u

In [21]:
art_feats = {}

# loop para obter as 'features' das músicas e adicionar à um novo dicio
for artist, songs in art_mus.items():
    if (len(songs) > 49):
        for song in songs:
            if artist not in art_feats.keys():
                art_feats[artist] = sp.audio_features(songs)
            else:
                art_feats[artist].append(sp.audio_features(songs))
    else:
        art_feats[artist] = sp.audio_features(songs)
        feats = sp.audio_features(songs)
art_feats

{'Ahmed Abdul-Malik': [{'acousticness': 0.00703,
   'analysis_url': 'https://api.spotify.com/v1/audio-analysis/6BIobfQex0fzhArSV7Le7t',
   'danceability': 0.583,
   'duration_ms': 360094,
   'energy': 0.532,
   'id': '6BIobfQex0fzhArSV7Le7t',
   'instrumentalness': 0.00326,
   'key': 5,
   'liveness': 0.0577,
   'loudness': -13.981,
   'mode': 0,
   'speechiness': 0.0417,
   'tempo': 99.0,
   'time_signature': 4,
   'track_href': 'https://api.spotify.com/v1/tracks/6BIobfQex0fzhArSV7Le7t',
   'type': 'audio_features',
   'uri': 'spotify:track:6BIobfQex0fzhArSV7Le7t',
   'valence': 0.827}],
 'Ana Lucia': [{'acousticness': 0.965,
   'analysis_url': 'https://api.spotify.com/v1/audio-analysis/6z1PPMeS4ZRMPGlXZayA10',
   'danceability': 0.596,
   'duration_ms': 138632,
   'energy': 0.393,
   'id': '6z1PPMeS4ZRMPGlXZayA10',
   'instrumentalness': 0,
   'key': 2,
   'liveness': 0.661,
   'loudness': -5.31,
   'mode': 1,
   'speechiness': 0.0484,
   'tempo': 112.411,
   'time_signature': 1,
   